In [1]:
# Import necessary libraries
import warnings
from vectorbtpro import *

warnings.filterwarnings("ignore")
vbt.settings.set_theme('dark')
vbt.settings.plotting.use_resampler=(True)
vbt.settings['plotting']['layout']['width']=600
vbt.settings['plotting']['layout']['height']=200



# Import data


In [4]:
m1_data_path = '/Users/ericervin/Documents/Coding/data-repository/data/m1_data.h5'
m1_data = vbt.BinanceData.from_hdf(m1_data_path)
m1_data.data['BTCUSDT'].tail()
resample_period = '1h'

# Resample data
m60_data = m1_data.resample(resample_period)
m30_data = m1_data.resample('30m')
# display(m60_data.data['BTCUSDT'].tail())

# Simply grab the BTC data
btc = m1_data.select('BTCUSDT')
# display(btc.get().tail())

h4_data = m60_data.resample('4h')
# data = h4_data.data['ETHUSDT']

data = m30_data

## Create SMA Cross Strategy

In [8]:
close = data.get('Close')
sma1 = data.run('sma', timeperiod=10)
sma2 = data.run('sma', timeperiod=500)
# The sma_timeperiod is a multiindex, so we need to drop it
sma1_cleaned = sma1.sma.droplevel('sma_timeperiod', axis=1)
sma2_cleaned = sma2.sma.droplevel('sma_timeperiod', axis=1)

# print(sma1_cleaned.tail())
# Set up your buy and sell signals
entries = (sma1_cleaned > sma2_cleaned)
exits = (sma1_cleaned < sma2_cleaned)

# Create multiple simulations one for each symbol
pf_sma = vbt.Portfolio.from_signals(close, entries, exits, init_cash=1000)
pf_buy_and_hold = vbt.Portfolio.from_holding(close, init_cash=1000)

# Create RSI mean reversion strategy
rsi = data.run('rsi', window=150)
# The RSI is a multiindex, so we need to drop it
rsi_cleaned = rsi.rsi.droplevel('rsi_window', axis=1)

# Set up your buy and sell signals
entries = (rsi_cleaned < 30)
exits = (rsi_cleaned > 70)
# Create multiple simulations one for each symbol
pf_rsi = vbt.Portfolio.from_signals(close, entries, exits, init_cash=1000)
pf_buy_and_hold = vbt.Portfolio.from_holding(close, init_cash=1000)

# Show all total returns for each strategy
pd.concat([pf_sma.total_return, pf_rsi.total_return, pf_buy_and_hold.total_return], axis=1, keys=['SMA', 'RSI', 'Buy and Hold'])
# Just grab a single simulation
# pf['AAPL'].stats()

SMA        RSI  Buy and Hold
symbol                                     
BTCUSDT   4.683011  10.558140       4.75364
ETHUSDT  11.944750   0.918152      20.26363

# Now let's build a portfolio of these strategies
For this demo I'll rebalance monthly based on equal weight and an alternate portfolio sim using a slightly different weighting strategy. Note later in the notebook we will create a rebalancing strategy based on regimes and a regime filter. However for learning purposes we will go one step at a time.

In [9]:
# Here we will treat each sim as a different asset
sma_strategy = pf_sma.value
rsi_strategy = pf_rsi.value


# Add _sma and _rsi to the end of each strategy
sma_strategy.columns = sma_strategy.columns + '_sma'
rsi_strategy.columns = rsi_strategy.columns + '_rsi'

# Single dataframe
strategy = pd.concat([sma_strategy, rsi_strategy], axis=1)



# Use Regime Filter for Weights
Let's look at the slope of the moving average of the SPY to set our regime. 

We will then create a dictionary of portfolio weights for each regime. Then apply that to our portfolio.

In [48]:
h1_data = m1_data.resample('1h')
h1_btc = h1_data.data['BTCUSDT']['Close']

def regime_detection(close, timeperiod=500):
    sma = vbt.talib("SMA").run(close, timeperiod=timeperiod).real
    # Bullish when sma is increasing
    bullish = np.full_like(sma, False) # create an array of False values
    bullish[1:] = sma.values[1:] > sma.values[:-1] # set the values to True if the sma is increasing
    return pd.Series(bullish, index=sma.index) # return a DataFrame with the regime

regime = regime_detection(h1_btc, timeperiod=50)

# Plot the regime
h1_btc.vbt.overlay_with_heatmap(regime).show()
    

Let's have a look at how each strategy performs

In [49]:
# Plot the various strategies
strategy.vbt.rebase(100).vbt.plot().show()
# Plot the regime
h1_btc.vbt.overlay_with_heatmap(regime).show()


In [43]:
strategy.columns


Index(['BTCUSDT_sma', 'ETHUSDT_sma', 'BTCUSDT_rsi', 'ETHUSDT_rsi'], dtype='object', name='symbol')

In [82]:
def create_regime_dict(bullish_btc_sma, bullish_btc_rsi, bullish_eth_sma, bullish_eth_rsi):
    # Round the sum to 6 decimal places to avoid floating-point precision issues
    total = round(bullish_btc_sma + bullish_btc_rsi + bullish_eth_sma + bullish_eth_rsi, 6)
    assert total == 1, f"Bullish weights must sum to 1, but they sum to {total}"
    
    # Calculate bearish weights as the inverse of bullish weights
    bearish_btc_sma = 1 - bullish_btc_sma
    bearish_btc_rsi = 1 - bullish_btc_rsi
    bearish_eth_sma = 1 - bullish_eth_sma
    bearish_eth_rsi = 1 - bullish_eth_rsi
    
    # Normalize bearish weights to sum to 1
    bearish_total = bearish_btc_sma + bearish_btc_rsi + bearish_eth_sma + bearish_eth_rsi
    bearish_btc_sma /= bearish_total
    bearish_btc_rsi /= bearish_total
    bearish_eth_sma /= bearish_total
    bearish_eth_rsi /= bearish_total
    
    return {
        'Bullish': {
            'BTCUSDT_sma': bullish_btc_sma,
            'ETHUSDT_sma': bullish_eth_sma,
            'BTCUSDT_rsi': bullish_btc_rsi,
            'ETHUSDT_rsi': bullish_eth_rsi
        },
        'Bearish': {
            'BTCUSDT_sma': bearish_btc_sma,
            'ETHUSDT_sma': bearish_eth_sma,
            'BTCUSDT_rsi': bearish_btc_rsi,
            'ETHUSDT_rsi': bearish_eth_rsi
        }
    }

# Example usage:
bullish_btc_sma = 0.1
bullish_eth_sma = 0.4
bullish_btc_rsi = 0.5
bullish_eth_rsi = 0.0

regime_dict = create_regime_dict(bullish_btc_sma, bullish_btc_rsi, bullish_eth_sma, bullish_eth_rsi)

# The rest of your code remains the same
def get_allocations(regime_value):
    if regime_value:
        return regime_dict['Bullish']
    else:
        return regime_dict['Bearish']

# Apply the function to each element of the regime Series
allocations = regime.apply(get_allocations)

# Convert the result to a DataFrame
allocations = pd.DataFrame(allocations.tolist(), index=regime.index)

# Set up the benchmark
bm = data.get('Close')['ETHUSDT']

# Create the portfolio with the new allocations
pf_w_regime = vbt.Portfolio.from_orders(
    strategy,
    size=allocations,
    size_type='target_percent',
    init_cash=1000,
    cash_sharing=True,
    bm_close=bm,
    leverage=1.0
)

# Plot the portfolio
pf_w_regime.plot(title='Regime-based Crypto Portfolio').show()

# Plot the allocations for a specific year
pf_w_regime['2023'].plot_allocations(height=500).show()

# Display portfolio statistics
print(pf_w_regime.stats())

Start Index                      2019-09-08 17:00:00+00:00
End Index                        2024-07-12 20:30:00+00:00
Total Duration                          1769 days 04:00:00
Start Value                                         1000.0
Min Value                                       938.717517
Max Value                                     16927.380497
End Value                                     13477.412615
Total Return [%]                               1247.741261
Benchmark Return [%]                           2026.363014
Position Coverage [%]                            99.997645
Max Gross Exposure [%]                               100.0
Max Drawdown [%]                                 61.332176
Max Drawdown Duration                    845 days 05:00:00
Total Orders                                         64577
Total Fees Paid                                        0.0
Total Trades                                         30630
Win Rate [%]                                     65.0667

In [73]:

pf_w_regime.stats()


Start Index                   2019-09-08 17:00:00+00:00
End Index                     2024-07-12 20:30:00+00:00
Total Duration                       1769 days 04:00:00
Start Value                                      1000.0
Min Value                                    999.649253
Max Value                                  31577.969514
End Value                                  27993.634162
Total Return [%]                            2699.363416
Benchmark Return [%]                        2026.363014
Position Coverage [%]                         97.623646
Max Gross Exposure [%]                            100.0
Max Drawdown [%]                              27.134156
Max Drawdown Duration                 196 days 19:30:00
Total Orders                                      51039
Total Fees Paid                                     0.0
Total Trades                                      25679
Win Rate [%]                                  44.444444
Best Trade [%]                                31

In [74]:
pf_w_regime.plot().show()

In [37]:
pf_w_regime['2020-01-01':'2020-01-31'].plot_allocations(height=500).show()